#### Libraries

In [1]:
import pandas as pd
import numpy as np
from sklearn.model_selection import KFold
from collections import defaultdict
from sklearn.metrics import mean_squared_error
from math import sqrt

from catboost import CatBoostRegressor, Pool

pd.set_option('display.max_columns', 500)

#### Read Data

In [2]:
data_dir = '/Users/konstantinivanov/Documents/work/PIK/files-pik_digital_day'
input_dir = '/Users/konstantinivanov/Documents/work/PIK/input'
output_dir = '/Users/konstantinivanov/Documents/work/PIK/output'
sub_dir = '/Users/konstantinivanov/Documents/work/PIK/sub'

In [3]:
#train
train_data = pd.read_csv(data_dir + "/train.csv")
train_data.drop(['start_square', 'plan_s', 'plan_m', 'plan_l', 'vid_0', 'vid_1', 'vid_2'], axis=1, inplace=True)
train_data.to_csv(input_dir + "/train_full.csv", index=False)

#test
test_data = pd.read_csv(data_dir + "/test.csv")
test_data['value'] = 0
test_data.to_csv(input_dir + "/test_.csv", index=False, columns = train_data.columns)

#### Validation

In [3]:
train_data = pd.read_csv(input_dir + "/train_full.csv")

K = 10

kf = KFold(n_splits=K, random_state=42, shuffle=True)
kf.get_n_splits(range(len(train_data)))

print(kf)  

for i, (train_index, valid_index) in enumerate(kf.split(range(len(train_data)))):
    train = train_data.loc[train_index]
    valid = train_data.loc[valid_index]

    train.to_csv(input_dir + f"/train_{i}.csv",index=False)
    valid.to_csv(input_dir + f"/valid_{i}.csv",index=False)

KFold(n_splits=10, random_state=42, shuffle=True)


#### Fit and Predict

In [8]:
TEST_FILE = input_dir + '/test_.csv' #add
CD_FILE = input_dir + '/train.txt'

test_pool = Pool(TEST_FILE, column_description=CD_FILE, has_header=True, delimiter=",")

In [9]:
test_data = pd.read_csv(TEST_FILE)

In [11]:
iterations = 5000
learning_rate = 0.05
depth = 8
random_seed = 42

Regressors = [
    CatBoostRegressor(iterations=iterations, learning_rate=learning_rate, depth=depth, random_seed=random_seed)
]

In [12]:
def FitOnKFolds(model):
    cum_y_test = np.zeros((len(test_data), 1))
    pred_y_train = np.zeros((len(train_data), 1))
    
    for i in range(K):
        TRAIN_FILE = input_dir + f'/train_{i}.csv'
        VAL_FILE = input_dir + f'/valid_{i}.csv'
        
        train_pool = Pool(TRAIN_FILE, column_description=CD_FILE, has_header=True, delimiter=",")
        val_pool = Pool(VAL_FILE, column_description=CD_FILE, has_header=True, delimiter=",")
        
        model.fit(train_pool, eval_set = val_pool)
        
        pred = model.predict(test_pool)
        cum_y_test += pred.reshape((len(test_data),1))
        
        pred = model.predict(val_pool)
        df = pd.read_csv(VAL_FILE)
        pred_y_train[df.id] = pred.reshape((len(df),1))
        
    return (cum_y_test/K).clip(int(min(train_data.value)), int(max(train_data.value))).reshape(-1),\
        sqrt(mean_squared_error(list(train_data['value']), list(pred_y_train)))

In [13]:
def write_ans(fl_name, y_test):
    dict_ans = defaultdict(list)
    dict_ans['id'] = list(range(len(y_test)))
    dict_ans['value'] = list(y_test)
    df_ans = pd.DataFrame.from_dict(dict_ans)
    df_ans.to_csv(sub_dir+'/'+fl_name+'.csv', index=False)
    return 'Answer /%s succesfully writed' % fl_name

In [14]:
%%time

vec_qual = []

for itr, model in enumerate(Regressors):
    y_test, qual = FitOnKFolds(model)
    vec_qual.append(qual)
    write_ans(f'subsub_ctb_itr={iterations}_lr={learning_rate}_depth={depth}_fld={K}_{itr}vers', y_test)

0:	learn: 450.5024333	test: 441.4696510	best: 441.4696510 (0)	total: 110ms	remaining: 9m 8s
1:	learn: 438.7915518	test: 429.3439164	best: 429.3439164 (1)	total: 156ms	remaining: 6m 30s
2:	learn: 427.6014582	test: 418.0251094	best: 418.0251094 (2)	total: 205ms	remaining: 5m 41s
3:	learn: 417.1351163	test: 407.4348378	best: 407.4348378 (3)	total: 259ms	remaining: 5m 23s
4:	learn: 407.9936673	test: 397.8959095	best: 397.8959095 (4)	total: 317ms	remaining: 5m 17s
5:	learn: 399.5838486	test: 389.3538899	best: 389.3538899 (5)	total: 368ms	remaining: 5m 6s
6:	learn: 390.5628974	test: 380.5746595	best: 380.5746595 (6)	total: 416ms	remaining: 4m 56s
7:	learn: 382.8787960	test: 372.8705748	best: 372.8705748 (7)	total: 438ms	remaining: 4m 33s
8:	learn: 375.5014484	test: 365.7714814	best: 365.7714814 (8)	total: 484ms	remaining: 4m 28s
9:	learn: 367.6024297	test: 358.1287707	best: 358.1287707 (9)	total: 541ms	remaining: 4m 30s
10:	learn: 362.6618994	test: 353.1264552	best: 353.1264552 (10)	total: 5

90:	learn: 231.8385924	test: 239.4759101	best: 239.4759101 (90)	total: 4.51s	remaining: 4m 3s
91:	learn: 231.0517111	test: 239.2234031	best: 239.2234031 (91)	total: 4.58s	remaining: 4m 4s
92:	learn: 230.7028763	test: 239.1624769	best: 239.1624769 (92)	total: 4.63s	remaining: 4m 4s
93:	learn: 230.4331945	test: 238.9351776	best: 238.9351776 (93)	total: 4.66s	remaining: 4m 3s
94:	learn: 229.8140508	test: 238.5485333	best: 238.5485333 (94)	total: 4.72s	remaining: 4m 3s
95:	learn: 229.2048428	test: 238.2097766	best: 238.2097766 (95)	total: 4.78s	remaining: 4m 4s
96:	learn: 228.7294407	test: 238.0682943	best: 238.0682943 (96)	total: 4.82s	remaining: 4m 3s
97:	learn: 228.6628122	test: 238.0588549	best: 238.0588549 (97)	total: 4.84s	remaining: 4m 1s
98:	learn: 228.4186653	test: 237.8841747	best: 237.8841747 (98)	total: 4.88s	remaining: 4m 1s
99:	learn: 227.7392879	test: 237.3936398	best: 237.3936398 (99)	total: 4.93s	remaining: 4m 1s
100:	learn: 227.3813603	test: 236.9556015	best: 236.9556015 

179:	learn: 204.4138138	test: 224.7550668	best: 224.7550668 (179)	total: 8.37s	remaining: 3m 44s
180:	learn: 204.1567025	test: 224.5933380	best: 224.5933380 (180)	total: 8.42s	remaining: 3m 44s
181:	learn: 203.8429208	test: 224.4107341	best: 224.4107341 (181)	total: 8.46s	remaining: 3m 44s
182:	learn: 203.8007135	test: 224.4439749	best: 224.4107341 (181)	total: 8.49s	remaining: 3m 43s
183:	learn: 203.5657394	test: 224.2127264	best: 224.2127264 (183)	total: 8.53s	remaining: 3m 43s
184:	learn: 203.2209602	test: 224.1658001	best: 224.1658001 (184)	total: 8.57s	remaining: 3m 43s
185:	learn: 203.1142469	test: 224.0862691	best: 224.0862691 (185)	total: 8.62s	remaining: 3m 43s
186:	learn: 202.7960342	test: 224.0463634	best: 224.0463634 (186)	total: 8.67s	remaining: 3m 43s
187:	learn: 202.6290835	test: 224.1079657	best: 224.0463634 (186)	total: 8.71s	remaining: 3m 42s
188:	learn: 202.3645631	test: 224.1323791	best: 224.0463634 (186)	total: 8.75s	remaining: 3m 42s
189:	learn: 202.2336443	test: 

264:	learn: 187.4388239	test: 217.5919552	best: 217.5919552 (264)	total: 12.2s	remaining: 3m 38s
265:	learn: 187.3206388	test: 217.5888495	best: 217.5888495 (265)	total: 12.3s	remaining: 3m 38s
266:	learn: 187.2271338	test: 217.5742966	best: 217.5742966 (266)	total: 12.3s	remaining: 3m 38s
267:	learn: 187.0694445	test: 217.5004109	best: 217.5004109 (267)	total: 12.4s	remaining: 3m 38s
268:	learn: 187.0130942	test: 217.4665352	best: 217.4665352 (268)	total: 12.4s	remaining: 3m 38s
269:	learn: 186.9081711	test: 217.4095018	best: 217.4095018 (269)	total: 12.4s	remaining: 3m 38s
270:	learn: 186.7941054	test: 217.3009988	best: 217.3009988 (270)	total: 12.5s	remaining: 3m 38s
271:	learn: 186.6197256	test: 217.1495383	best: 217.1495383 (271)	total: 12.5s	remaining: 3m 37s
272:	learn: 186.5507527	test: 217.1402781	best: 217.1402781 (272)	total: 12.6s	remaining: 3m 37s
273:	learn: 186.3097850	test: 217.1471666	best: 217.1402781 (272)	total: 12.6s	remaining: 3m 37s
274:	learn: 186.0595068	test: 

353:	learn: 174.7003837	test: 210.9924048	best: 210.9924048 (353)	total: 16.3s	remaining: 3m 34s
354:	learn: 174.4764150	test: 210.6344578	best: 210.6344578 (354)	total: 16.4s	remaining: 3m 33s
355:	learn: 174.3771626	test: 210.6167284	best: 210.6167284 (355)	total: 16.4s	remaining: 3m 33s
356:	learn: 174.2923705	test: 210.6333685	best: 210.6167284 (355)	total: 16.4s	remaining: 3m 33s
357:	learn: 174.2438582	test: 210.5373549	best: 210.5373549 (357)	total: 16.5s	remaining: 3m 33s
358:	learn: 173.9599964	test: 210.3695879	best: 210.3695879 (358)	total: 16.5s	remaining: 3m 33s
359:	learn: 173.9018670	test: 210.4112673	best: 210.3695879 (358)	total: 16.6s	remaining: 3m 33s
360:	learn: 173.7781303	test: 210.3844799	best: 210.3695879 (358)	total: 16.6s	remaining: 3m 33s
361:	learn: 173.5131623	test: 210.1786914	best: 210.1786914 (361)	total: 16.7s	remaining: 3m 33s
362:	learn: 173.3162760	test: 210.1255711	best: 210.1255711 (362)	total: 16.7s	remaining: 3m 33s
363:	learn: 173.2779198	test: 

...

4581:	learn: 73.2006697	test: 223.3619082	best: 223.3093857 (4570)	total: 3m 44s	remaining: 20.5s
4582:	learn: 73.1980770	test: 223.3720590	best: 223.3093857 (4570)	total: 3m 44s	remaining: 20.4s
4583:	learn: 73.1867765	test: 223.3901274	best: 223.3093857 (4570)	total: 3m 44s	remaining: 20.4s
4584:	learn: 73.1842888	test: 223.3847094	best: 223.3093857 (4570)	total: 3m 44s	remaining: 20.3s
4585:	learn: 73.1623798	test: 223.3998198	best: 223.3093857 (4570)	total: 3m 44s	remaining: 20.3s
4586:	learn: 73.1613411	test: 223.4074847	best: 223.3093857 (4570)	total: 3m 44s	remaining: 20.2s
4587:	learn: 73.1609701	test: 223.4082798	best: 223.3093857 (4570)	total: 3m 44s	remaining: 20.2s
4588:	learn: 73.1603354	test: 223.4063306	best: 223.3093857 (4570)	total: 3m 44s	remaining: 20.1s
4589:	learn: 73.1509370	test: 223.4023767	best: 223.3093857 (4570)	total: 3m 44s	remaining: 20.1s
4590:	learn: 73.1497695	test: 223.4064500	best: 223.3093857 (4570)	total: 3m 44s	remaining: 20s
4591:	learn: 73.133800

4667:	learn: 72.6922546	test: 223.3075525	best: 223.3075525 (4667)	total: 3m 48s	remaining: 16.3s
4668:	learn: 72.6892107	test: 223.3067032	best: 223.3067032 (4668)	total: 3m 48s	remaining: 16.2s
4669:	learn: 72.6716896	test: 223.2883594	best: 223.2883594 (4669)	total: 3m 48s	remaining: 16.2s
4670:	learn: 72.6707299	test: 223.2899763	best: 223.2883594 (4669)	total: 3m 48s	remaining: 16.1s
4671:	learn: 72.6658403	test: 223.2919387	best: 223.2883594 (4669)	total: 3m 48s	remaining: 16.1s
4672:	learn: 72.6629923	test: 223.2938272	best: 223.2883594 (4669)	total: 3m 48s	remaining: 16s
4673:	learn: 72.6575322	test: 223.2998619	best: 223.2883594 (4669)	total: 3m 48s	remaining: 16s
4674:	learn: 72.6424726	test: 223.2999554	best: 223.2883594 (4669)	total: 3m 48s	remaining: 15.9s
4675:	learn: 72.6357555	test: 223.3108116	best: 223.2883594 (4669)	total: 3m 48s	remaining: 15.9s
4676:	learn: 72.6311070	test: 223.3104375	best: 223.2883594 (4669)	total: 3m 49s	remaining: 15.8s
4677:	learn: 72.6260796	

4752:	learn: 72.0805281	test: 223.1368863	best: 223.1317748 (4751)	total: 3m 52s	remaining: 12.1s
4753:	learn: 72.0722732	test: 223.0844436	best: 223.0844436 (4753)	total: 3m 52s	remaining: 12s
4754:	learn: 72.0500030	test: 223.1323519	best: 223.0844436 (4753)	total: 3m 52s	remaining: 12s
4755:	learn: 72.0332976	test: 223.1411432	best: 223.0844436 (4753)	total: 3m 52s	remaining: 11.9s
4756:	learn: 72.0299622	test: 223.1376195	best: 223.0844436 (4753)	total: 3m 52s	remaining: 11.9s
4757:	learn: 72.0276942	test: 223.1390840	best: 223.0844436 (4753)	total: 3m 52s	remaining: 11.8s
4758:	learn: 72.0268095	test: 223.1429828	best: 223.0844436 (4753)	total: 3m 53s	remaining: 11.8s
4759:	learn: 72.0219504	test: 223.1587754	best: 223.0844436 (4753)	total: 3m 53s	remaining: 11.8s
4760:	learn: 72.0203373	test: 223.1654989	best: 223.0844436 (4753)	total: 3m 53s	remaining: 11.7s
4761:	learn: 72.0137027	test: 223.1680557	best: 223.0844436 (4753)	total: 3m 53s	remaining: 11.7s
4762:	learn: 72.0111669	

4839:	learn: 71.4057328	test: 223.1608059	best: 223.0392018 (4798)	total: 3m 57s	remaining: 7.83s
4840:	learn: 71.3893454	test: 223.1493585	best: 223.0392018 (4798)	total: 3m 57s	remaining: 7.79s
4841:	learn: 71.3833498	test: 223.1525320	best: 223.0392018 (4798)	total: 3m 57s	remaining: 7.74s
4842:	learn: 71.3735293	test: 223.1390603	best: 223.0392018 (4798)	total: 3m 57s	remaining: 7.69s
4843:	learn: 71.3661012	test: 223.1399490	best: 223.0392018 (4798)	total: 3m 57s	remaining: 7.64s
4844:	learn: 71.3629307	test: 223.1380661	best: 223.0392018 (4798)	total: 3m 57s	remaining: 7.59s
4845:	learn: 71.3432821	test: 223.1491199	best: 223.0392018 (4798)	total: 3m 57s	remaining: 7.54s
4846:	learn: 71.3140542	test: 223.1784915	best: 223.0392018 (4798)	total: 3m 57s	remaining: 7.49s
4847:	learn: 71.2935895	test: 223.1904175	best: 223.0392018 (4798)	total: 3m 57s	remaining: 7.44s
4848:	learn: 71.2909208	test: 223.1918923	best: 223.0392018 (4798)	total: 3m 57s	remaining: 7.39s
4849:	learn: 71.2791

4928:	learn: 70.6921981	test: 223.0703314	best: 223.0012033 (4912)	total: 4m 1s	remaining: 3.48s
4929:	learn: 70.6847095	test: 223.0752808	best: 223.0012033 (4912)	total: 4m 1s	remaining: 3.43s
4930:	learn: 70.6613139	test: 223.0661810	best: 223.0012033 (4912)	total: 4m 1s	remaining: 3.38s
4931:	learn: 70.6608908	test: 223.0653257	best: 223.0012033 (4912)	total: 4m 1s	remaining: 3.33s
4932:	learn: 70.6599478	test: 223.0630922	best: 223.0012033 (4912)	total: 4m 1s	remaining: 3.28s
4933:	learn: 70.6576904	test: 223.0474839	best: 223.0012033 (4912)	total: 4m 1s	remaining: 3.23s
4934:	learn: 70.6571302	test: 223.0482592	best: 223.0012033 (4912)	total: 4m 1s	remaining: 3.18s
4935:	learn: 70.6558412	test: 223.0453685	best: 223.0012033 (4912)	total: 4m 1s	remaining: 3.13s
4936:	learn: 70.6553567	test: 223.0441791	best: 223.0012033 (4912)	total: 4m 1s	remaining: 3.08s
4937:	learn: 70.6440655	test: 223.0436184	best: 223.0012033 (4912)	total: 4m 1s	remaining: 3.03s
4938:	learn: 70.6420499	test: 

In [10]:
print(vec_qual)

[225.1491584601252]


In [15]:
y_test

array([8.46464802e+02, 1.13613222e+03, 1.81489713e+02, 5.72522611e+02,
       3.67510091e+01, 6.56536270e+01, 7.05104526e+01, 3.10965817e+02,
       3.52878746e+02, 3.86794087e+02, 5.22895415e+02, 3.88584427e+02,
       1.46401943e+02, 5.42282450e+01, 1.76765000e+02, 3.49618439e+02,
       1.18998910e+03, 4.34503443e+01, 3.94013064e+01, 1.37014932e+02,
       5.88641323e+02, 9.97774352e+01, 1.47438077e+02, 3.35979308e+02,
       3.64012481e+02, 1.60268509e+02, 1.98059837e+02, 3.28799541e+02,
       1.47060276e+02, 5.26889617e+02, 3.84608198e+01, 1.63724372e+02,
       2.81345409e+02, 2.89695649e+02, 1.98544437e+02, 2.31624173e+00,
       2.52797771e+02, 2.62599898e+02, 4.84555429e+02, 2.38261673e+02,
       4.58564114e+01, 3.99901847e+01, 4.72923375e+02, 3.39857198e+02,
       1.15303572e+02, 9.42269310e+02, 7.31467823e+02, 1.09270642e+03,
       4.70696074e+01, 2.59532982e+02, 1.06895925e+02, 3.16306024e+02,
       0.00000000e+00, 2.96218093e+02, 2.17536490e+02, 0.00000000e+00,
      

In [17]:
test_data['value'] = y_test

In [20]:
test_data.shape

(525, 51)

In [22]:
usefull_test_data = test_data[['bulk_id', 'spalen', 'date1', 'value']]

In [19]:
full_test_data = pd.read_csv(data_dir + "/test.csv")

In [24]:
merg_test_data = pd.merge(full_test_data, usefull_test_data, how='left', on=['bulk_id', 'spalen', 'date1'])

In [25]:
merg_test_data

id                               bulk_id  spalen       date1  \
0        0  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-02-01   
1        1  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-02-01   
2        2  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-02-01   
3        3  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-02-01   
4        4  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-03-01   
5        5  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-03-01   
6        6  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-03-01   
7        7  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-03-01   
8        8  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-04-01   
9        9  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-04-01   
10      10  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-04-01   
11      11  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-04-01   
12      12  F07BF3C7-C905-E811-893D-00505688958B       2  2018-04-01   
13      13  F07BF3C7-C905-E811-893D-00505688958B       3  2018-04-01   
14      14  F07BF3C7-C905-E811-893D-00505688958B       0  2018-04-01   
15      15  F07BF3C7-C905-E811-893D-00505688958B       1  2018-04-01   
16      16  7726CF5A-CC0A-E511-8098-001EC9D56418       3  2018-02-01   
17      17  7726CF5A-CC0A-E511-8098-001EC9D56418       3  2018-03-01   
18      18  7726CF5A-CC0A-E511-8098-001EC9D56418       3  2018-04-01   
19      19  72B1CAF6-A2DC-E511-9840-001EC9D56418       2  2018-02-01   
20      20  72B1CAF6-A2DC-E511-9840-001EC9D56418       3  2018-02-01   
21      21  35168781-8F60-E611-9523-001EC9D5643C       3  2018-02-01   
22      22  35168781-8F60-E611-9523-001EC9D5643C       2  2018-02-01   
23      23  A8632090-8F60-E611-9523-001EC9D5643C       3  2018-02-01   
24      24  A8632090-8F60-E611-9523-001EC9D5643C       2  2018-02-01   
25      25  50B329EC-1DE2-E511-B953-001EC9D56418       3  2018-02-01   
26      26  F4BE45B2-AFF2-E611-84D2-001EC9D56418       3  2018-02-01   
27      27  F4BE45B2-AFF2-E611-84D2-001EC9D56418       4  2018-02-01   
28      28  F4BE45B2-AFF2-E611-84D2-001EC9D56418       1  2018-02-01   
29      29  F4BE45B2-AFF2-E611-84D2-001EC9D56418       2  2018-02-01   
...    ...                                   ...     ...         ...   
1740  1740  C0B1362A-C378-E511-B4A4-001EC9D5643C       3  2018-03-01   
1741  1741  C0B1362A-C378-E511-B4A4-001EC9D5643C       1  2018-03-01   
1742  1742  999F708D-4FE9-E711-B9FF-00505688958B       0  2018-03-01   
1743  1743  999F708D-4FE9-E711-B9FF-00505688958B       1  2018-03-01   
1744  1744  999F708D-4FE9-E711-B9FF-00505688958B       2  2018-03-01   
1745  1745  999F708D-4FE9-E711-B9FF-00505688958B       3  2018-03-01   
1746  1746  999F708D-4FE9-E711-B9FF-00505688958B       4  2018-03-01   
1747  1747  AECE8386-7E98-E711-8530-00505688958B       2  2018-03-01   
1748  1748  AECE8386-7E98-E711-8530-00505688958B       1  2018-03-01   
1749  1749  AECE8386-7E98-E711-8530-00505688958B       4  2018-03-01   
1750  1750  AECE8386-7E98-E711-8530-00505688958B       0  2018-03-01   
1751  1751  8CEB3310-63E8-E611-B887-001EC9D5643C       4  2018-04-01   
1752  1752  8CEB3310-63E8-E611-B887-001EC9D5643C       2  2018-04-01   
1753  1753  8CEB3310-63E8-E611-B887-001EC9D5643C       3  2018-04-01   
1754  1754  8CEB3310-63E8-E611-B887-001EC9D5643C       1  2018-04-01   
1755  1755  8CEB3310-63E8-E611-B887-001EC9D5643C       0  2018-04-01   
1756  1756  8B5D0C0E-C378-E511-B4A4-001EC9D5643C       2  2018-04-01   
1757  1757  8B5D0C0E-C378-E511-B4A4-001EC9D5643C       1  2018-04-01   
1758  1758  C0B1362A-C378-E511-B4A4-001EC9D5643C       2  2018-04-01   
1759  1759  C0B1362A-C378-E511-B4A4-001EC9D5643C       4  2018-04-01   
1760  1760  C0B1362A-C378-E511-B4A4-001EC9D5643C       1  2018-04-01   
1761  1761  999F708D-4FE9-E711-B9FF-00505688958B       1  2018-04-01   
1762  1762  999F708D-4FE9-E711-B9FF-00505688958B       0  2018-04-01   
1763  1763  999F708D-4FE9-E711-B9FF-00505688958B

In [26]:
last_y_test = pd.read_csv(sub_dir + "/sub_ctb_5000itr_10fld_0vrs.csv")

In [32]:
last_y_test['new_value'] = merg_test_data['value']

In [43]:
last_y_test

id       value    new_value  new_new_value
0        0  671.202126   846.464802     671.202126
1        1  901.201359  1136.132217     901.201359
2        2  173.424232   181.489713     173.424232
3        3  526.875810   572.522611     526.875810
4        4  671.382423          NaN     671.382423
5        5  897.893392          NaN     897.893392
6        6  160.393575          NaN     160.393575
7        7  505.486410          NaN     505.486410
8        8  635.830416          NaN     635.830416
9        9  872.204362          NaN     872.204362
10      10  167.355687          NaN     167.355687
11      11  486.272858          NaN     486.272858
12      12  479.067304          NaN     479.067304
13      13  235.393616          NaN     235.393616
14      14   73.095419          NaN      73.095419
15      15  312.726368          NaN     312.726368
16      16   49.948933    36.751009      49.948933
17      17   50.654814          NaN      50.654814
18      18   42.353674          NaN      42.353674
19      19  291.354300    65.653627     291.354300
20      20   69.172892    70.510453      69.172892
21      21  152.201684   310.965817     152.201684
22      22  517.538238   352.878746     517.538238
23      23  245.986883   386.794087     245.986883
24      24  540.102016   522.895415     540.102016
25      25   82.936715          NaN      82.936715
26      26  329.838840   388.584427     329.838840
27      27  206.667318   146.401943     206.667318
28      28   87.263004    54.228245      87.263004
29      29  414.592143   176.765000     414.592143
...    ...         ...          ...            ...
1740  1740  432.359192          NaN     432.359192
1741  1741   88.644147          NaN      88.644147
1742  1742    0.000000          NaN       0.000000
1743  1743  184.755808          NaN     184.755808
1744  1744  469.154141          NaN     469.154141
1745  1745  359.373758          NaN     359.373758
1746  1746   50.329822          NaN      50.329822
1747  1747  232.003969          NaN     232.003969
1748  1748   59.430137          NaN      59.430137
1749  1749   40.719584          NaN      40.719584
1750  1750    0.000000          NaN       0.000000
1751  1751  125.105142          NaN     125.105142
1752  1752  800.207613          NaN     800.207613
1753  1753  681.621117          NaN     681.621117
1754  1754  407.237909          NaN     407.237909
1755  1755    0.000000          NaN       0.000000
1756  1756  215.840473          NaN     215.840473
1757  1757  140.896958          NaN     140.896958
1758  1758  258.811681          NaN     258.811681
1759  1759   87.581409          NaN      87.581409
1760  1760   93.829515          NaN      93.829515
1761  1761  163.561567          NaN     163.561567
1762  1762    0.000000          NaN       0.000000
1763  1763   47.136548          NaN      47.136548
1764  1764  465.630787          NaN     465.630787
1765  1765  353.818908          NaN     353.818908
1766  1766  238.326258          NaN     238.326258
1767  1767   60.438260          NaN      60.438260
1768  1768    0.000000          NaN       0.000000
1769  1769   41.978350          NaN      41.978350

[1770 rows x 4 columns]

In [28]:
len(last_y_test)

1770

In [29]:
len(merg_test_data)

1770

In [41]:
last_y_test['new_value'][4] > 0

False

In [42]:
last_y_test['new_new_value'] = last_y_test['value']

In [44]:
for itr in range(len(last_y_test)):
    if last_y_test['new_value'][itr] > 0:
        last_y_test['new_new_value'][itr] = last_y_test['new_value'][itr]

/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  This is separate from the ipykernel package so we can avoid doing imports until


In [45]:
last_y_test

id       value    new_value  new_new_value
0        0  671.202126   846.464802     846.464802
1        1  901.201359  1136.132217    1136.132217
2        2  173.424232   181.489713     181.489713
3        3  526.875810   572.522611     572.522611
4        4  671.382423          NaN     671.382423
5        5  897.893392          NaN     897.893392
6        6  160.393575          NaN     160.393575
7        7  505.486410          NaN     505.486410
8        8  635.830416          NaN     635.830416
9        9  872.204362          NaN     872.204362
10      10  167.355687          NaN     167.355687
11      11  486.272858          NaN     486.272858
12      12  479.067304          NaN     479.067304
13      13  235.393616          NaN     235.393616
14      14   73.095419          NaN      73.095419
15      15  312.726368          NaN     312.726368
16      16   49.948933    36.751009      36.751009
17      17   50.654814          NaN      50.654814
18      18   42.353674          NaN      42.353674
19      19  291.354300    65.653627      65.653627
20      20   69.172892    70.510453      70.510453
21      21  152.201684   310.965817     310.965817
22      22  517.538238   352.878746     352.878746
23      23  245.986883   386.794087     386.794087
24      24  540.102016   522.895415     522.895415
25      25   82.936715          NaN      82.936715
26      26  329.838840   388.584427     388.584427
27      27  206.667318   146.401943     146.401943
28      28   87.263004    54.228245      54.228245
29      29  414.592143   176.765000     176.765000
...    ...         ...          ...            ...
1740  1740  432.359192          NaN     432.359192
1741  1741   88.644147          NaN      88.644147
1742  1742    0.000000          NaN       0.000000
1743  1743  184.755808          NaN     184.755808
1744  1744  469.154141          NaN     469.154141
1745  1745  359.373758          NaN     359.373758
1746  1746   50.329822          NaN      50.329822
1747  1747  232.003969          NaN     232.003969
1748  1748   59.430137          NaN      59.430137
1749  1749   40.719584          NaN      40.719584
1750  1750    0.000000          NaN       0.000000
1751  1751  125.105142          NaN     125.105142
1752  1752  800.207613          NaN     800.207613
1753  1753  681.621117          NaN     681.621117
1754  1754  407.237909          NaN     407.237909
1755  1755    0.000000          NaN       0.000000
1756  1756  215.840473          NaN     215.840473
1757  1757  140.896958          NaN     140.896958
1758  1758  258.811681          NaN     258.811681
1759  1759   87.581409          NaN      87.581409
1760  1760   93.829515          NaN      93.829515
1761  1761  163.561567          NaN     163.561567
1762  1762    0.000000          NaN       0.000000
1763  1763   47.136548          NaN      47.136548
1764  1764  465.630787          NaN     465.630787
1765  1765  353.818908          NaN     353.818908
1766  1766  238.326258          NaN     238.326258
1767  1767   60.438260          NaN      60.438260
1768  1768    0.000000          NaN       0.000000
1769  1769   41.978350          NaN      41.978350

[1770 rows x 4 columns]

In [46]:
new_y_test = last_y_test[['id', 'new_new_value']]

In [49]:
new_y_test = new_y_test.rename(index=str, columns={"new_new_value": "value"})

In [52]:
new_y_test['value'].values

array([ 846.46480162, 1136.13221665,  181.48971268, ...,   60.43826009,
          0.        ,   41.97835011])

In [53]:
write_ans(f'sub_merge_vers', new_y_test['value'].values)

'Answer /sub_merge_vers succesfully writed'